In [2]:
import pandas as pd
import os
import gc
import json
import cv2
from tqdm.auto import tqdm
from HCFA_OCR_XML_to_DataFrame import *

In [3]:
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')
gc.collect()

34

In [4]:
HCFA_final_keys = pd.read_excel(r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_Keys_list_verification.xlsx", sheet_name = 'Field_Names from KEY file')

In [6]:
key_names = HCFA_final_keys['Key_Name'].tolist()
len(key_names)

157

In [7]:
def generate_ground_truth(row):
    ground_truth = ''
    try:
        if "?" not in str(row["OCR_Optimizer"]):
            ground_truth = row["OCR_Optimizer"]
        else:
            ground_truth = row["Data"]
    except:
        ground_truth = row["Data"]
    return ground_truth

In [8]:
folder_path = r"D:\Xelp_work\FSL Project\Sprint_2\HCFA_data\train\key"

In [11]:
import gc
gc.collect()

0

In [14]:
c = 0
overal_data = pd.DataFrame()
for filename in tqdm(os.listdir(folder_path)):
    if filename.endswith(".KEY"):
        file_path = os.path.join(folder_path, filename)
        try:
            df, single_fields, grp_field_names, table_field_names, images = OCR_XML_to_DataFrame(file_path, key_names)
            df["Ground_truth"] = df.apply(generate_ground_truth, axis=1)
            df.replace(to_replace=[None], value='[BLANK]', inplace=True)
            df["Image_Name"] = images * len(df)
            df["XML_File"] = filename
            overal_data = pd.concat([overal_data, df], ignore_index=True)
        except Exception as e:
            raise e
    c += 1
    if c % 100 == 0:
        gc.collect()

  0%|          | 0/27919 [00:00<?, ?it/s]

MemoryError: Unable to allocate 26.0 MiB for an array with shape (1, 3408809) and data type object

In [ ]:
overal_data.to_excel("HCFA_BSC_Test_GRND_T_from XML.xlsx", index=False)